# Data Shed Data Science Interview Task

A single database has been provided, with the task being to answer the following questions:

- Please review the quality of the data, and present any issues
- Which artist in this data set lived the longest?
- Who are the top 10 artists by the number of artworks?
- Which artist is created the most artwork by total surface area?
- Did any artists have artwork acquired during their lifetime?
- Please group the artworks into as many clusters as you feel is appropriate, using attributes from both the artist and artworks tables, and assign each artwork to this new cluster.
- Identify other potential areas of value within the dataset and how you went about describing and evaluating that use of data

## Data Loading and inspection

In [1]:
#Imports 

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import sqlite3
import matplotlib.pyplot as plt

# Input data files are available in the "../data/" directory.
# For example, running this (by clicking run or pressing Shift+Enter) will list the files in the input directory

path = "../data/"  #Insert path here
database = path + 'artists.db'

/var/folders/y_/6q_c570s5ldfvhx_3g9k76y40000gn/T/ipykernel_48180/3621859982.py:4: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)


As the dataset is small, we can load the entire thing into a pandas dataframe for inspection, then join the two tables to get a flat dataset. This is the preferred option as it is easier to handle all of the processing in processing rather than seperating the load and transformation logic over SQL and python. In reality if the dataset was too large to keep in working memory there are a few options:

1. Load a select portion into memory for the task, either limited by rows, columns or a custom query for doing some basic feature engineering or tranformations
2. Use spark, either locally or a local/remote cluster. Spark indexes the data and we can then perform joins/analysis with a similiar style as with Pandas. This can also be done over data in cold storage(AWS S3/Azure blob), without the need for a local copy of the data or a database
3. Use a remote machine (databricks/aws sagemaker/ azure machine learning workspace) to perform the analysis with a larger memory capacity 

All of the above options are valid in the right set of circumstances, but as there are no specific constraints on this task I will load the entire dataset into memory and perform the analysis in pandas. I am quite comfortable in SQL, but prefer pandas for the flexibility and ease of use.

In [2]:
conn = sqlite3.connect(database)

tables = pd.read_sql("""SELECT *
                        FROM sqlite_master
                        WHERE type='table';""", conn)

In [3]:
tables

type      name  tbl_name  rootpage  \
0  table   artists   artists         2   
1  table  artworks  artworks       159   

                                                 sql  
0  CREATE TABLE "artists" (\n"Artist ID" INTEGER,...  
1  CREATE TABLE "artworks" (\n"Artwork ID" INTEGE...

In [4]:
artists = pd.read_sql("""SELECT *
                        FROM artists;""", conn)

artworks = pd.read_sql("""SELECT *
                        FROM artworks;""", conn)


Check for duplicate keys in each table:

Im aware there may be duplicates, but will inspect manually in the next step

## Artists Quality inspection

In [30]:
artists

In [31]:
artists['Name'] = artists['Name'].str.lower()
artists['Nationality'] = artists['Nationality'].str.lower()
artists['Gender'] = artists['Gender'].str.lower()
artists['age'] = artists['Death Year'] - artists['Birth Year']
artists['death_before_birth_or_under_10'] = artists['age'] < 10

In [32]:
artists[artists['death_before_birth_or_under_10']]

Artist ID                                         Name Nationality  \
2122        2377                                     gruppo n        None   
8496       11125        neal small designs inc., new york, ny        None   
9644       26812                          archizoom associati     italian   
10553      29983                        gorgona artists group    croatian   
11278      32944       nice style the world's first pose band        None   
11801      35469            cada (colectivo acciones de arte)     chilean   
12109      36946                                hi red center        None   
12437      38170  united democratic front (udf), south africa        None   
12496      38423                      save the press campaign        None   
14245      47019                                 joy division     british   
14303      47218                            grey organisation     british   
14570      48051                               memphis, milan        None   
14918      49496                            joshua light show    american   

      Gender  Birth Year  Death Year  age  death_before_birth_or_under_10  
2122    None      1959.0      1964.0  5.0                            True  
8496    None      1965.0      1973.0  8.0                            True  
9644    None      1966.0      1974.0  8.0                            True  
10553   None      1959.0      1966.0  7.0                            True  
11278   None      1971.0      1975.0  4.0                            True  
11801   None      1979.0      1985.0  6.0                            True  
12109   None      1963.0      1964.0  1.0                            True  
12437   None      1983.0      1991.0  8.0                            True  
12496   None      1988.0      1990.0  2.0                            True  
14245   None      1976.0      1980.0  4.0                            True  
14303   None      1983.0      1991.0  8.0                            True  
14570   None      1981.0      1985.0  4.0                            True  
14918   None      1967.0      1970.0  3.0                            True

In [33]:
artists.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15091 entries, 0 to 15090
Data columns (total 8 columns):
 #   Column                          Non-Null Count  Dtype  
---  ------                          --------------  -----  
 0   Artist ID                       15091 non-null  int64  
 1   Name                            15091 non-null  object 
 2   Nationality                     12603 non-null  object 
 3   Gender                          12019 non-null  object 
 4   Birth Year                      11237 non-null  float64
 5   Death Year                      4579 non-null   float64
 6   age                             4566 non-null   float64
 7   death_before_birth_or_under_10  15091 non-null  bool   
dtypes: bool(1), float64(3), int64(1), object(3)
memory usage: 840.2+ KB


In [34]:
artists.describe()

Artist ID    Birth Year   Death Year          age
count  15091.000000  11237.000000  4579.000000  4566.000000
mean   18297.556027   1930.852719  1974.287399    72.325011
std    16632.963898     34.531997    31.153665    15.948683
min        1.000000   1730.000000  1795.000000     1.000000
25%     4195.500000   1910.000000  1958.000000    64.000000
50%     8593.000000   1936.000000  1980.000000    75.000000
75%    33088.500000   1956.000000  1998.000000    83.000000
max    67695.000000   2012.000000  2017.000000   130.000000

In [35]:
# Use plotly to create a horizontal bar chart of the nationality of the artists, displaying the top 10 nationalities with the most artists
import plotly.express as px
import plotly.graph_objects as go

px.bar(artists
         .groupby('Nationality')
            .size()
            .sort_values(ascending=False)
            .head(30)
            .reset_index(name='count'),
         x='count',
            y='Nationality',
            orientation='h',
            title='Top 20 Nationalities of Artists',
            height=1000,
)






In [36]:
px.bar(artists
         .groupby('Gender')
            .size()
            .sort_values(ascending=False)
            .reset_index(name='count'),
         x='count',
            y='Gender',
            orientation='h',
            title='Gender Distribution of Artists',
            height=500,
)

In [37]:
# The first value counts counts the number of times each unique id appears, the second counts how many 2x duplicates, 3x duplicates, etc.
artist_duplicate_counts = artists['Artist ID'].value_counts().value_counts()
artist_duplicate_counts_by_name = artists['Name'].value_counts().value_counts()
if artist_duplicate_counts.shape[0] > 1:
    print('There are duplicate Artist IDs')

if artist_duplicate_counts_by_name.shape[0] > 1:
    print('There are duplicate Artist Names')


There are duplicate Artist Names


In [38]:
px.bar(artists
         .groupby('Name')
            .size()
            .sort_values(ascending=False)
            .head(30)
            .reset_index(name='count'),
         x='count',
            y='Name',
            orientation='h',
            title='Top Duplicate Artist Names',
            height=1000,
)

In [39]:
# Create a histogram of the birth years of artists, with 20 bins
px.histogram(artists, x='Birth Year', nbins=20, title='Birth Year Distribution of Artists')

In [40]:
# Create a histogram of the birth years of artists, with 20 bins
px.histogram(artists, x='Death Year', nbins=20, title='Death Year Distribution of Artists')

In [41]:
missing_data_labels = ['unknown', 'none', 'unknown designer', 'various artists', 'unknown artist', 'nationality unknown', None]
artists = artists.replace(missing_data_labels, np.nan)

In [42]:
artists.isna().sum()

Artist ID                             0
Name                                 42
Nationality                        2747
Gender                             3072
Birth Year                         3854
Death Year                        10512
age                               10525
death_before_birth_or_under_10        0
dtype: int64

In [221]:
def load_artists():
    artists = pd.read_sql("""SELECT *
                            FROM artists;""", conn)
    artists['Name'] = artists['Name'].str.lower()
    artists['Nationality'] = artists['Nationality'].str.lower()
    artists['Gender'] = artists['Gender'].str.lower()
    artists['age'] = artists['Death Year'] - artists['Birth Year']
    artists['death_before_birth_or_under_10'] = artists['age'] < 10
    missing_data_labels = ['unknown', 'none', 'unknown designer', 'various artists', 'unknown artist', 'nationality unknown', None]
    artists = artists.replace(missing_data_labels, np.nan)
    return artists

In [203]:
artists = load_artists()

Some of the issues with the data include:

- Many different names for missing values, None, NaN, Unknown Designer, Various Artists, Unknown Artist, Nationality unknown, Unknown designer
- Not an issue but to be aware of - some artists are actually organisations, not individuals
- Male has a duplicate label 'male' (have now lower cased everything)
- Duplicate artists, but not a huge number so not a huge issue
- There could be additional duplicate artists, with slightly different variations on their name. This could be checked by using a fuzzy matching algorithm to check for similar names, and then manually inspecting the results
- Lots of missing data - even some artists with missing names
- Heavily biased towards american/western artists (not sure if this is a sampling bias or a true reflection of the art world)
- Heavily biased towards male artists (not sure if this is a sampling bias or a true reflection of the art world)

## Artworks Quality inspection

In [59]:
# The first value counts counts the number of times each unique id appears, the second counts how many 2x duplicates, 3x duplicates, etc.
artworks_duplicate_counts = artworks['Artwork ID'].value_counts().value_counts()
artworks_duplicate_counts_by_name = artworks['Title'].value_counts().value_counts()
if artworks_duplicate_counts.shape[0] > 1:
    print('There are duplicate Artwork IDs')

if artworks_duplicate_counts_by_name.shape[0] > 1:
    print('There are duplicate Artwork Names')

There are duplicate Artwork Names


In [49]:
# Show all columns
pd.set_option('display.max_columns', None)
artworks.head(7)

Artwork ID                                              Title Artist ID  \
0           2  Ferdinandsbrücke Project, Vienna, Austria, Ele...      6210   
1           3  City of Music, National Superior Conservatory ...      7470   
2           4  Villa near Vienna Project, Outside Vienna, Aus...      7605   
3           5  The Manhattan Transcripts Project, New York, N...      7056   
4           6  Villa, project, outside Vienna, Austria, Exter...      7605   
5           7  The Manhattan Transcripts Project, New York, N...      7056   
6           8  The Manhattan Transcripts Project, New York, N...      7056   

                       Name     Date  \
0               Otto Wagner     1896   
1  Christian de Portzamparc     1987   
2                Emil Hoppe     1903   
3           Bernard Tschumi     1980   
4                Emil Hoppe     1903   
5           Bernard Tschumi  1976-77   
6           Bernard Tschumi  1976-77   

                                              Medium  \
0      Ink and cut-and-pasted painted pages on paper   
1                  Paint and colored pencil on print   
2  Graphite, pen, color pencil, ink, and gouache ...   
3  Photographic reproduction with colored synthet...   
4  Graphite, color pencil, ink, and gouache on tr...   
5                          Gelatin silver photograph   
6                         Gelatin silver photographs   

                           Dimensions Acquisition Date  \
0  19 1/8 x 66 1/2" (48.6 x 168.9 cm)       1996-04-09   
1       16 x 11 3/4" (40.6 x 29.8 cm)       1995-01-17   
2   13 1/2 x 12 1/2" (34.3 x 31.8 cm)       1997-01-15   
3           20 x 20" (50.8 x 50.8 cm)       1995-01-17   
4    15 1/8 x 7 1/2" (38.4 x 19.1 cm)       1997-01-15   
5           14 x 18" (35.6 x 45.7 cm)       1995-01-17   
6     Each: 14 x 18" (35.6 x 45.7 cm)       1995-01-17   

                                              Credit Catalogue  \
0  Fractional and promised gift of Jo Carole and ...         Y   
1  Gift of the architect in honor of Lily Auchinc...         Y   
2             Gift of Jo Carole and Ronald S. Lauder         Y   
3  Purchase and partial gift of the architect in ...         Y   
4             Gift of Jo Carole and Ronald S. Lauder         Y   
5  Purchase and partial gift of the architect in ...         Y   
6  Purchase and partial gift of the architect in ...         Y   

              Department Classification Object Number  Diameter (cm)  \
0  Architecture & Design   Architecture      885.1996            NaN   
1  Architecture & Design   Architecture        1.1995            NaN   
2  Architecture & Design   Architecture        1.1997            NaN   
3  Architecture & Design   Architecture        2.1995            NaN   
4  Architecture & Design   Architecture        2.1997            NaN   
5  Architecture & Design   Architecture      3.1995.1            NaN   
6  Architecture & Design   Architecture   3.1995.1-24            NaN   

   Circumference (cm)  Height (cm)  Length (cm)  Width (cm)  Depth (cm)  \
0                 NaN      48.6000          NaN    168.9000         NaN   
1                 NaN      40.6401          NaN     29.8451         NaN   
2                 NaN      34.3000          NaN     31.8000         NaN   
3                 NaN      50.8000          NaN     50.8000         NaN   
4                 NaN      38.4000          NaN     19.1000         NaN   
5                 NaN      35.6000          NaN     45.7000         NaN   
6                 NaN      35.6000          NaN     45.7000         NaN   

   Weight (kg)  Duration (s)  
0          NaN           NaN  
1          NaN           NaN  
2          NaN           NaN  
3          NaN           NaN  
4          NaN           NaN  
5          NaN           NaN  
6          NaN           NaN

In [44]:
artworks.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 130262 entries, 0 to 130261
Data columns (total 21 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   Artwork ID          130262 non-null  int64  
 1   Title               130210 non-null  object 
 2   Artist ID           128802 non-null  object 
 3   Name                128802 non-null  object 
 4   Date                127954 non-null  object 
 5   Medium              118343 non-null  object 
 6   Dimensions          118799 non-null  object 
 7   Acquisition Date    124799 non-null  object 
 8   Credit              127192 non-null  object 
 9   Catalogue           130262 non-null  object 
 10  Department          130262 non-null  object 
 11  Classification      130262 non-null  object 
 12  Object Number       130262 non-null  object 
 13  Diameter (cm)       1399 non-null    float64
 14  Circumference (cm)  10 non-null      float64
 15  Height (cm)         111893 non-nul

In [51]:
artworks.describe()

Artwork ID  Diameter (cm)  Circumference (cm)    Height (cm)  \
count  130262.000000    1399.000000           10.000000  111893.000000   
mean    82501.371636      23.248939           44.868020      37.712992   
std     58124.331702      45.460079           28.631604      48.151347   
min         2.000000       0.635000            9.900000       0.000000   
25%     34171.250000       7.900000           23.500000      18.100000   
50%     69541.500000      13.700000           36.000000      27.940056   
75%    128955.750000      24.782500           71.125000      44.450100   
max    218011.000000     914.400000           83.800000    9140.000000   

       Length (cm)     Width (cm)    Depth (cm)    Weight (kg)  Duration (s)  
count   736.000000  111003.000000  11443.000000     298.000000  3.084000e+03  
mean     89.117417      38.176838     18.291359    1248.278691  7.830060e+03  
std     329.717487      67.250118     57.703925   11856.456824  1.185046e+05  
min       0.000000       0.000000      0.000000       0.090000  0.000000e+00  
25%      17.031875      17.800000      0.000000       5.443200  2.100000e+02  
50%      26.700000      25.400100      0.700000      19.051100  7.200000e+02  
75%      79.100000      44.800000     13.335013      65.318000  3.613250e+03  
max    8321.056600    9144.000000   1808.483617  185067.585957  6.283065e+06

In [52]:
# Sort by 'Weight (kg)'
artworks.sort_values(by='Weight (kg)', ascending=False).head(10)

Artwork ID                                            Title Artist ID  \
75033        80990                                           Switch      5349   
124062      193590                                            Equal      5349   
75464        81514                                  Intersection II      5349   
74825        80742                               Torqued Ellipse IV      5349   
87539       101921                                       Delineator      5349   
75074        81039                                          Moondog      5494   
75502        81555                                   Broken Obelisk      4285   
86966       100313                                              WWI      5349   
75683        81818  Eight-Sided Plane of Six Masses and Four Scales      4779   
75417        81458                                            Above      3537   

                      Name                    Date  \
75033        Richard Serra                    1999   
124062       Richard Serra                    2015   
75464        Richard Serra                 1992-93   
74825        Richard Serra                    1998   
87539        Richard Serra                 1974-75   
75074           Tony Smith  1964 (fabricated 1998)   
75502       Barnett Newman                 1963-69   
86966        Richard Serra                    1984   
75683    David Rabinowitch                    1972   
75417   Alexander Liberman                    1970   

                                                   Medium  \
75033                      Weatherproof steel, six plates   
124062            Forged weatherproof steel, eight blocks   
75464   Weatherproof steel, four identical conical sec...   
74825                                  Weatherproof steel   
87539                                    Hot-rolled steel   
75074                                    Painted aluminum   
75502                                       Cor-Ten steel   
86966                                       Cor-Ten steel   
75683   Hot-rolled steel, mild steel, pickled and oile...   
75417                                       Painted steel   

                                               Dimensions Acquisition Date  \
75033      each 13' 6" x 52' x 2" (411.5 x 1585 x 5.1 cm)       2000-02-07   
124062      Each 60 x 66 x 72" (152.4 x 167.6 x 182.9 cm)       2015-06-01   
75464   Two sections 13' 1 1/2" (400 cm) high x 51' 9"...       1998-05-01   
74825   12' 3" x 26' 6" x 32' 6" (373.4 x 807.7 x 990....       1999-02-08   
87539   Two plates, each: 1" x 10' x 26' (2.5 cm x 3.1...       2012-06-04   
75074   17' 1 1/4" x 15' 8 1/2" x 13' 7 1/4" (521.3 x ...       1998-03-09   
75502   24' 7 1/4" x 10' 5 1/2" x 10' 5 1/2" (749.9 x ...       1971-10-12   
86966              55 x 64 x 8" (139.7 x 162.6 x 20.3 cm)       2005-10-06   
75683   overall 3" x 8' 7" x 6' 5/8" (7.6 x 261.7 x 18...       1977-10-18   
75417   12' 10 5/8" x 11' 7 1/4" x 9' 1 1/8" (394.6 x ...       1971-05-11   

                                                   Credit Catalogue  \
75033          Gift of Emily Carroll and Thomas W. Weisel         Y   
124062      Purchase and Enid A. Haupt Fund (by exchange)         Y   
75464              Gift of Jo Carole and Ronald S. Lauder         Y   
74825   Fractional and promised gift of Leon and Debra...         Y   
87539   Gift of Edward R. Broida and Gift of Mr. and M...         Y   
75074   Gift of Agnes Gund, Helen Acheson Bequest (by ...         Y   
75502                                   Given anonymously         Y   
86966                            Gift of Edward R. Broida         Y   
75683                       Gift of J. Frederic Byers III         Y   
75417                             A. Conger Goodyear Fund         Y   

                  Department Classification Object Number  Diameter (cm)  \
75033   Painting & Sculpture      Sculpture  125.2000.a-f            NaN   
124062  Painting & Sculpture      Sculpture  504.2015.a-

In [54]:
px.bar(artworks
         .groupby('Department')
            .size()
            .sort_values(ascending=False)
            .head(30)
            .reset_index(name='count'),
         x='count',
            y='Department',
            orientation='h',
            title='Department',
            height=1000,
)

In [55]:
px.bar(artworks
         .groupby('Classification')
            .size()
            .sort_values(ascending=False)
            .head(30)
            .reset_index(name='count'),
         x='count',
            y='Classification',
            orientation='h',
            title='Classification',
            height=1000,
)

In [57]:
px.bar(artworks
         .groupby('Title')
            .size()
            .sort_values(ascending=False)
            .head(30)
            .reset_index(name='count'),
         x='count',
            y='Title',
            orientation='h',
            title='Title',
            height=1000,
)

In [72]:
# Identify the rows in the Artist ID column that arent integers

artworks['Artist ID Numeric'] = pd.to_numeric(artworks['Artist ID'], errors='coerce')
artworks[artworks['Artist ID Numeric'].isna()]

Artwork ID                                              Title  \
65              81  house iv transformation study, project, falls ...   
66              82  villa dall'ava, paris (saint-cloud), france, e...   
76             100  regional administrative center, project "tries...   
107            148  woodland crematorium, woodland cemetery, stock...   
110            151  palais de la découverte project, paris, france...   
...            ...                                                ...   
130243      217969             untitled sound poetry collaboration...   
130246      217972                  judson church, ray gun specs, etc   
130255      217981                                    fluxus festival   
130258      217984   fluxus-manifestatie in en rond kunsthandel monet   
130260      217986                                       unidentified   

               Artist ID                                          Name  Date  \
65            6969, 8134                   peter eisenman, robert cole  1975   
66            6956, 6957             rem koolhaas, madelon vriesendorp  1987   
76      7661, 8131, 8180     aldo rossi, gianni braghieri, m. bosshard  1974   
107            27, 24452         erik gunnar asplund, sigurd lewerentz  1937   
110     8102, 6703, 4312  paul nelson, frantz jourdain, oscar nitzchke  1938   
...                  ...                                           ...   ...   
130243       42821, 2928                       earl brown, ray johnson  None   
130246              None                                          None  None   
130255              None                                          None  1962   
130258              None                                          None  1962   
130260              None                                          None  None   

                                                Medium  \
65          ink and color ink on frosted polymer sheet   
66            synthetic polymer paint and ink on paper   
76                 rubbed ink and pastel on whiteprint   
107                          graphite on tracing paper   
110     ink and color pencil on paper mounted on board   
...                                                ...   
130243                                        cassette   
130246                                        cassette   
130255                                      audio reel   
130258                                             vhs   
130260                                        cassette   

                                           Dimensions Acquisition Date  \
65                 13 3/4 x 44 5/8" (34.9 x 113.3 cm)       1980-01-08   
66                          25 x 39" (63.5 x 99.1 cm)       2000-01-19   
76                      28 1/2 x 36" (72.4 x 91.4 cm)       1980-01-08   
107                 16 1/4 x 37 7/8" (41.3 x 96.2 cm)       1990-01-17   
110     14 3/4 x 37 1/2 x 1/2" (37.5 x 95.3 x 1.3 cm)       1966-01-01   
...                                               ...              ...   
130243                                           None       2008-10-08   
130246                                           None       2008-10-08   
130255                                           None       2008-10-08   
130258                                           None       2008-10-08   
130260                                           None       2008-10-08   

                                                   Credit Catalogue  \
65                                 gift of philip johnson         y   
66                                  gift of max underwood         y   
76                                    philip johnson fund         y   
107     gift of blanchette hooker rockefeller, mrs. gi...         y   
110                                gift of the architects         y   
...                                                   ...       ...   
130243  the gilbert and lila silverman fluxus collecti...         n   
130246  the gilb

Some issues are:

1. Incorrectly formatted dates, the acuisition date column has not been parsed as a date by pandas, implying that there is inconsistent formatting. The 'Date' column does not have a consistent format either. Both will need to be parsed for any reasonable analysis
2. Some outliers in the weight column, with one piece labelled as having a weight of 125 tonnes. This is possible, but unlikely given the dimensions of the piece
3. (not assigned) is a label in the classification column.
4. Untitled is used to label missing titles
5. Some artists work on art together and all the ids are listed together in the artist column. This will need to be split out into seperate rows for each artist


In [204]:
def load_artworks():
    # Load the artworks dataset
    artworks = pd.read_sql("""SELECT *
                            FROM artworks;""", conn)

    # Force the column 'Acquisition Date' to be a datetime with the format 'YYYY-MM-DD'
    artworks['Acquisition Date'] = pd.to_datetime(artworks['Acquisition Date'], format='%Y-%m-%d', errors='coerce')

    # Use regexp to extract the first 4 consecutive digits from the 'Date' column and store it in a new column called 'Year'
    artworks['Year'] = artworks['Date'].str.extract(r'(\b\d{4}\b)', expand=True).astype(float)

    # lower case all of the object columns
    artworks = artworks.apply(lambda x: x.str.lower() if x.dtype == "object" else x)

    # Replace 'untitled' with NaN
    artworks = artworks.replace('untitled', np.nan)
    # Split the 'Artist ID' column into a list '1049, 1050' -> ['1049', '1050']
    artworks['Artist ID'] = artworks['Artist ID'].str.split(',')
    # Explode the list into separate rows
    artworks = artworks.explode('Artist ID')
    artworks['Artist ID'] = pd.to_numeric(artworks['Artist ID'], errors='coerce')

    return artworks
artworks = load_artworks()

In [65]:
# Create a histogram of the 'Year' column, with 20 bins
px.histogram(artworks, x='Year', nbins=20, title='Year Distribution of Artworks')

## Question 1 - Which artist lived the longest?

In [69]:
# Sort the artists column by age
artists = artists.sort_values(by='age', ascending=False)
artists.head(10)

Artist ID                                               Name  \
12486      38294  union paper bag machine company, philadelphia, pa   
3449        3844                                      leni matthaei   
9164       23931                                          b. efimov   
13568      43532                                 manoel de oliveira   
9306       24431                                    horacio coppola   
1549        1750                                          hans erni   
7136        8103                                     oscar niemeyer   
9725       27127                                      beatrice wood   
6051        6735                                        agnes lyall   
5885        6556                                         eva zeisel   

      Nationality  Gender  Birth Year  Death Year    age  \
12486         NaN     NaN      1869.0      1999.0  130.0   
3449       german  female      1873.0      1981.0  108.0   
9164      russian    male      1900.0      2008.0  108.0   
13568  portuguese     NaN      1908.0      2015.0  107.0   
9306    argentine    male      1906.0      2012.0  106.0   
1549        swiss    male      1909.0      2015.0  106.0   
7136    brazilian    male      1907.0      2012.0  105.0   
9725     american  female      1893.0      1998.0  105.0   
6051     american  female      1908.0      2013.0  105.0   
5885     american  female      1906.0      2011.0  105.0   

       death_before_birth_or_under_10  
12486                           False  
3449                            False  
9164                            False  
13568                           False  
9306                            False  
1549                            False  
7136                            False  
9725                            False  
6051                            False  
5885                            False

The artist with the longest lifespan is clearly an incorrect value as the artist name doesnt make any sense '	union paper bag machine company, philadelphia, pa', and lives longer than the worlds oldest person.

After this record there are two artists who lived to 108:

Leni Matthaei (1873-1981) and B. Efiimov (1900-2008)

## Question 2 - Who are the top 10 artists by the number of artworks?

In [210]:
def add_number_of_artist_works(artists, artworks):
    # Coalesce the Artist Name columns 'Name_artist' and 'Name_artwork' into a new column 'Name'
    joined_artists_artworks = pd.merge(artists, artworks, on='Artist ID', how='inner', suffixes=('_artist', '_artwork'))
    joined_artists_artworks['Name'] = joined_artists_artworks['Name_artist'].combine_first(joined_artists_artworks['Name_artwork'])

    # Count the number of artworks per Artist ID
    artworks_per_artist = joined_artists_artworks['Artist ID'].value_counts().reset_index(name='Number of Artworks')

    # Merge the 'artworks_per_artist' dataframe with the 'artists' dataframe on the 'Artist ID' column
    artists = pd.merge(artists, artworks_per_artist, left_on='Artist ID', right_on='Artist ID', how='left')
    return artists

artists = add_number_of_artist_works(artists, artworks)


In [93]:
# Sort the artists by the number of artworks
artists = artists.sort_values(by='Number of Artworks', ascending=False)

artists.head(11)

Artist ID                      Name Nationality  Gender  Birth Year  \
2883        229              eugène atget      french    male      1857.0   
42          710          louise bourgeois    american  female      1911.0   
1213       7166  ludwig mies van der rohe    american    male      1886.0   
8734       8595      unknown photographer         NaN     NaN         NaN   
1113       1633             jean dubuffet      french    male      1901.0   
5387       2002           lee friedlander    american    male      1934.0   
331        4609             pablo picasso     spanish    male      1881.0   
55         1055              marc chagall      french    male      1887.0   
956        3832             henri matisse      french    male      1869.0   
1606        665            pierre bonnard      french    male      1867.0   
4211      21398           george maciunas    american    male      1931.0   

      Death Year   age  death_before_birth_or_under_10   count  \
2883      1927.0  70.0                           False  5050.0   
42        2010.0  99.0                           False  3363.0   
1213      1969.0  83.0                           False  2595.0   
8734         NaN   NaN                           False  1656.0   
1113      1985.0  84.0                           False  1436.0   
5387         NaN   NaN                           False  1335.0   
331       1973.0  92.0                           False  1323.0   
55        1985.0  98.0                           False  1174.0   
956       1954.0  85.0                           False  1069.0   
1606      1947.0  80.0                           False   909.0   
4211      1978.0  47.0                           False   903.0   

      Number of Artworks  
2883              5050.0  
42                3363.0  
1213              2595.0  
8734              1656.0  
1113              1436.0  
5387              1335.0  
331               1323.0  
55                1174.0  
956               1069.0  
1606               909.0  
4211               903.0

The top 10 artists by the number of artworks are shown above, 11 is used as there is a name of 'unknown photographer' which could be a mix of artists

## Question 3 - Which artist is created the most artwork by total surface area?

In [124]:
from itertools import combinations

joined_artists_artworks = pd.merge(artists, artworks, on='Artist ID', how='inner', suffixes=('_artist', '_artwork'))

all_dimensions = ["Diameter (cm)", "Height (cm)", "Length (cm)", "Width (cm)", "Depth (cm)", "Circumference (cm)"]
dimensions = joined_artists_artworks[all_dimensions]

# Get all the posible combinations of multiple dimensions, for instance, 'Height (cm)' and 'Width (cm)' or 'Height (cm)', 'Width (cm)' and 'Depth (cm)'
dimension_combinations_output = []
for i in range(2, 7):
    dimension_combinations = list(combinations(dimensions.columns, i))
    for combination in dimension_combinations:
        non_selected_dimensions = [dimension for dimension in all_dimensions if dimension not in combination]
        # Count the number of artworks that have all the selected dimensions, and none of the non-selected dimensions
        artworks_with_required_dimensions = joined_artists_artworks[joined_artists_artworks[non_selected_dimensions].isna().all(axis=1)]
        artworks_with_all_dimensions = artworks_with_required_dimensions[~artworks_with_required_dimensions[list(combination)].isna().any(axis=1)]
        dimension_combinations_output.append({'Dimension Combination': combination, 'Number of Artworks': artworks_with_all_dimensions.shape[0]})

dimension_combinations_output = pd.DataFrame(dimension_combinations_output)
# Sort the dimension_combinations dataframe by the 'Number of Artworks' column
dimension_combinations_output = dimension_combinations_output.sort_values(by='Number of Artworks', ascending=False)

# Display all the column text
pd.set_option('display.max_colwidth', None)
dimension_combinations_output = dimension_combinations_output[dimension_combinations_output['Number of Artworks'] > 0]

In [128]:
list(dimension_combinations_output['Dimension Combination'])

[('Height (cm)', 'Width (cm)'),
 ('Height (cm)', 'Width (cm)', 'Depth (cm)'),
 ('Diameter (cm)', 'Height (cm)'),
 ('Length (cm)', 'Width (cm)'),
 ('Height (cm)', 'Length (cm)', 'Width (cm)'),
 ('Diameter (cm)', 'Height (cm)', 'Width (cm)'),
 ('Diameter (cm)', 'Height (cm)', 'Width (cm)', 'Depth (cm)'),
 ('Diameter (cm)', 'Length (cm)'),
 ('Height (cm)', 'Length (cm)', 'Width (cm)', 'Depth (cm)'),
 ('Width (cm)', 'Depth (cm)'),
 ('Diameter (cm)', 'Depth (cm)'),
 ('Length (cm)', 'Width (cm)', 'Depth (cm)'),
 ('Height (cm)', 'Depth (cm)'),
 ('Height (cm)', 'Length (cm)'),
 ('Diameter (cm)', 'Height (cm)', 'Circumference (cm)'),
 ('Height (cm)', 'Length (cm)', 'Depth (cm)'),
 ('Diameter (cm)', 'Circumference (cm)'),
 ('Diameter (cm)', 'Width (cm)', 'Depth (cm)'),
 ('Diameter (cm)', 'Height (cm)', 'Length (cm)'),
 ('Diameter (cm)', 'Height (cm)', 'Depth (cm)'),
 ('Diameter (cm)', 'Width (cm)'),
 ('Height (cm)', 'Length (cm)', 'Circumference (cm)'),
 ('Diameter (cm)', 'Height (cm)', 'Length 

In [140]:
import math


# I generated the below with chat gpt to save time
def surface_area(row):
    kwargs = row.to_dict()
    # remove nan values
    kwargs = {k: v for k, v in kwargs.items() if not np.isnan(v)}
    if 'Height (cm)' in kwargs and 'Width (cm)' in kwargs:
        # Surface area of a rectangle (2D object)
        return kwargs['Height (cm)'] * kwargs['Width (cm)']
    elif 'Height (cm)' in kwargs and 'Width (cm)' in kwargs and 'Depth (cm)' in kwargs:
        # Surface area of a box (3D object)
        return 2 * (kwargs['Height (cm)'] * kwargs['Width (cm)'] + kwargs['Height (cm)'] * kwargs['Depth (cm)'] + kwargs['Width (cm)'] * kwargs['Depth (cm)'])
    elif 'Diameter (cm)' in kwargs and 'Height (cm)' in kwargs:
        # Surface area of a cylinder (2D object)
        return 2 * math.pi * kwargs['Diameter (cm)'] * (kwargs['Diameter (cm)'] / 2 + kwargs['Height (cm)'])
    elif 'Length (cm)' in kwargs and 'Width (cm)' in kwargs:
        # Surface area of a rectangle (2D object)
        return kwargs['Length (cm)'] * kwargs['Width (cm)']
    elif 'Height (cm)' in kwargs and 'Length (cm)' in kwargs and 'Width (cm)' in kwargs:
        # Surface area of a rectangular prism (3D object)
        return 2 * (kwargs['Height (cm)'] * kwargs['Length (cm)'] + kwargs['Height (cm)'] * kwargs['Width (cm)'] + kwargs['Length (cm)'] * kwargs['Width (cm)'])
    elif 'Diameter (cm)' in kwargs and 'Height (cm)' in kwargs and 'Width (cm)' in kwargs:
        # Surface area of a cone (3D object)
        return math.pi * kwargs['Diameter (cm)'] * (kwargs['Diameter (cm)'] / 2 + kwargs['Height (cm)'])
    elif 'Diameter (cm)' in kwargs and 'Height (cm)' in kwargs and 'Width (cm)' in kwargs and 'Depth (cm)' in kwargs:
        # Surface area of a box (3D object)
        return 2 * (kwargs['Height (cm)'] * kwargs['Width (cm)'] + kwargs['Height (cm)'] * kwargs['Depth (cm)'] + kwargs['Width (cm)'] * kwargs['Depth (cm)'])
    elif 'Diameter (cm)' in kwargs and 'Length (cm)' in kwargs:
        # Surface area of a cylinder (2D object)
        return math.pi * kwargs['Diameter (cm)'] * kwargs['Length (cm)']
    elif 'Height (cm)' in kwargs and 'Length (cm)' in kwargs and 'Width (cm)' in kwargs and 'Depth (cm)' in kwargs:
        # Surface area of a rectangular prism (3D object)
        return 2 * (kwargs['Height (cm)'] * kwargs['Length (cm)'] + kwargs['Height (cm)'] * kwargs['Width (cm)'] + kwargs['Length (cm)'] * kwargs['Width (cm)'])
    elif 'Width (cm)' in kwargs and 'Depth (cm)' in kwargs:
        # Surface area of a rectangle (2D object)
        return kwargs['Width (cm)'] * kwargs['Depth (cm)']
    elif 'Diameter (cm)' in kwargs and 'Depth (cm)' in kwargs:
        # Surface area of a cylinder (2D object)
        return math.pi * kwargs['Diameter (cm)'] * kwargs['Depth (cm)']
    elif 'Length (cm)' in kwargs and 'Width (cm)' in kwargs and 'Depth (cm)' in kwargs:
        # Surface area of a rectangular prism (3D object)
        return 2 * (kwargs['Length (cm)'] * kwargs['Width (cm)'] + kwargs['Length (cm)'] * kwargs['Depth (cm)'] + kwargs['Width (cm)'] * kwargs['Depth (cm)'])
    elif 'Height (cm)' in kwargs and 'Depth (cm)' in kwargs:
        # Surface area of a rectangle (2D object)
        return kwargs['Height (cm)'] * kwargs['Depth (cm)']
    elif 'Height (cm)' in kwargs and 'Length (cm)' in kwargs:
        # Surface area of a rectangle (2D object)
        return kwargs['Height (cm)'] * kwargs['Length (cm)']
    elif 'Diameter (cm)' in kwargs and 'Height (cm)' in kwargs and 'Circumference (cm)' in kwargs:
        # Surface area of a cone (3D object)
        return math.pi * kwargs['Diameter (cm)'] * (kwargs['Diameter (cm)'] / 2 + kwargs['Height (cm)'])
    elif 'Height (cm)' in kwargs and 'Length (cm)' in kwargs and 'Depth (cm)' in kwargs:
        # Surface area of a rectangular prism (3D object)
        return 2 * (kwargs['Height (cm)'] * kwargs['Length (cm)'] + kwargs['Height (cm)'] * kwargs['Depth (cm)'] + kwargs['Length (cm)'] * kwargs['Depth (cm)'])
    elif 'Diameter (cm)' in kwargs and 'Circumference (cm)' in kwargs:
        # Surface area of a cylinder (2D object)
        return math.pi * kwargs['Diameter (cm)'] * kwargs['Circumference (cm)']
    elif 'Diameter (cm)' in kwargs and 'Width (cm)' in kwargs and 'Depth (cm)' in kwargs:
        # Surface area of a rectangular prism (3D object)
        return 2 * (kwargs['Width (cm)'] * kwargs['Depth (cm)'] + kwargs['Diameter (cm)'] * kwargs['Depth (cm)'] + kwargs['Diameter (cm)'] * kwargs['Width (cm)'])
    elif 'Diameter (cm)' in kwargs and 'Height (cm)' in kwargs and 'Length (cm)' in kwargs:
        # Surface area of a rectangular prism (3D object)
        return 2 * (kwargs['Height (cm)'] * kwargs['Length (cm)'] + kwargs['Height (cm)'] * kwargs['Diameter (cm)'] + kwargs['Length (cm)'] * kwargs['Diameter (cm)'])
    elif 'Diameter (cm)' in kwargs and 'Height (cm)' in kwargs and 'Depth (cm)' in kwargs:
        # Surface area of a cylindrical segment (3D object)
        return 2 * (kwargs['Diameter (cm)'] * kwargs['Height (cm)'] + math.pi * (kwargs['Diameter (cm)'] / 2) ** 2)
    elif 'Diameter (cm)' in kwargs and 'Width (cm)' in kwargs:
        # Surface area of a cylinder (2D object)
        return math.pi * kwargs['Diameter (cm)'] * kwargs['Width (cm)']
    elif 'Height (cm)' in kwargs and 'Length (cm)' in kwargs and 'Circumference (cm)' in kwargs:
        # Surface area of a cylindrical segment (3D object)
        return kwargs['Circumference (cm)'] * (kwargs['Height (cm)'] + kwargs['Length (cm)'])
    elif 'Diameter (cm)' in kwargs and 'Height (cm)' in kwargs and 'Length (cm)' in kwargs and 'Width (cm)' in kwargs:
        # Surface area of a rectangular prism (3D object)
        return 2 * (kwargs['Height (cm)'] * kwargs['Length (cm)'] + kwargs['Height (cm)'] * kwargs['Width (cm)'] + kwargs['Length (cm)'] * kwargs['Width (cm)'])
    elif 'Diameter (cm)' in kwargs:
        # Surface area of a circle (2D object)
        return math.pi * (kwargs['Diameter (cm)'] / 2) ** 2
    else:
        print(f"Invalid combination of dimensions provided: {kwargs}")
        return None

# Example usage:
# Specify the dimensions you have for the artwork
dimensions = {
    'Height (cm)': 10,
    'Width (cm)': 5,
    'Depth (cm)': np.nan
    # Add more dimensions as needed
}

# Calculate the surface area based on the available dimensions
area = surface_area(pd.Series(dimensions))
print("Surface Area:", area)


Surface Area: 50.0


In [209]:
def add_surface_area_to_joined_artworks(joined_artists_artworks):
    joined_artists_artworks['Surface Area (cm^2)'] = joined_artists_artworks[all_dimensions].apply(surface_area, axis=1)
    return joined_artists_artworks

joined_artists_artworks = add_surface_area_to_joined_artworks(joined_artists_artworks)

In [142]:

joined_artists_artworks['Surface Area (cm^2)'].isna().sum()

19593

All of the missing values are due to missing dimensions in the data.

In [143]:
# Group by Artist ID and calculate the total surface area of all the artworks per artist
total_surface_area_per_artist = joined_artists_artworks.groupby('Artist ID')['Surface Area (cm^2)'].sum().reset_index(name='Total Surface Area')



# Merge the 'total_surface_area_per_artist' dataframe with the 'artists' dataframe on the 'Artist ID' column
artists = pd.merge(artists, total_surface_area_per_artist, left_on='Artist ID', right_on='Artist ID', how='left')

# Sort the artists by the total surface area
artists = artists.sort_values(by='Total Surface Area', ascending=False)

artists.head(10)

Artist ID                      Name Nationality  Gender  Birth Year  \
994        902           james lee byars    american    male      1932.0   
209        922          alexander calder    american    male      1898.0   
2         7166  ludwig mies van der rohe    american    male      1886.0   
257       5349             richard serra    american    male      1938.0   
1          710          louise bourgeois    american  female      1911.0   
12        6459        frank lloyd wright    american    male      1867.0   
11        8059               lilly reich      german  female      1885.0   
34        4823       robert rauschenberg    american    male      1925.0   
63        3048           ellsworth kelly    american    male      1923.0   
6         4609             pablo picasso     spanish    male      1881.0   

     Death Year   age  death_before_birth_or_under_10   count  \
994      1997.0  65.0                           False    24.0   
209      1976.0  78.0                           False   100.0   
2        1969.0  83.0                           False  2595.0   
257         NaN   NaN                           False    83.0   
1        2010.0  99.0                           False  3363.0   
12       1959.0  92.0                           False   803.0   
11       1947.0  62.0                           False   839.0   
34       2008.0  83.0                           False   361.0   
63       2015.0  92.0                           False   256.0   
6        1973.0  92.0                           False  1323.0   

     Number of Artworks  Total Surface Area  
994                24.0        1.035273e+07  
209               100.0        9.633515e+06  
2                2595.0        7.819024e+06  
257                83.0        4.606000e+06  
1                3363.0        4.529469e+06  
12                803.0        3.013036e+06  
11                839.0        2.817420e+06  
34                361.0        2.817297e+06  
63                256.0        2.513885e+06  
6                1323.0        2.193162e+06

Its difficult to give a precise answer to this wuestion. THe top artists are sculptors and architects, who will natually have a larger surface area than painters per piece. The estimates for surface area I used are based on the volume taken up by the sculpture. In reality some sculptors/architects may have a large volume but a small surface area, and vice versa.

## Question 4 - Did any artists have artwork acquired during their lifetime?



In [225]:
def add_artworks_aquired_before_death(artists, artworks):
    joined_artists_artworks = pd.merge(artists, artworks, on='Artist ID', how='inner', suffixes=('_artist', '_artwork'))
    artworks_acquired_before_death = joined_artists_artworks[joined_artists_artworks['Acquisition Date'].dt.year < joined_artists_artworks['Death Year']]
    # Group by Artist ID and calculate the number of artworks acquired before the artist's death
    artworks_acquired_before_death = artworks_acquired_before_death.groupby('Artist ID').size().reset_index(name='Number of Artworks Acquired Before Death')

    # Merge the 'artworks_acquired_before_death' dataframe with the 'artists' dataframe on the 'Artist ID' column
    artists = pd.merge(artists, artworks_acquired_before_death, left_on='Artist ID', right_on='Artist ID', how='left')

    # Sort the artists by the number of artworks acquired before death
    artists = artists.sort_values(by='Number of Artworks Acquired Before Death', ascending=False)
    return artists

artists = add_artworks_aquired_before_death(artists, artworks)
artists.head(10)

Artist ID                       Name Nationality  Gender  Birth Year  \
631         710           louise bourgeois    american  female      1911.0   
1449       1633              jean dubuffet      french    male      1901.0   
944        1055               marc chagall      french    male      1887.0   
4136       4609              pablo picasso     spanish    male      1881.0   
3157       3528                 sol lewitt    american    male      1928.0   
3610       4016                  joan miró     spanish    male      1893.0   
3428       3821               andré masson      french    male      1896.0   
52           60                ansel adams    american    male      1902.0   
4327       4823        robert rauschenberg    american    male      1925.0   
4768       5318  andré dunoyer de segonzac      french    male      1884.0   

      Death Year   age  death_before_birth_or_under_10  Number of Artworks  \
631       2010.0  99.0                           False              3363.0   
1449      1985.0  84.0                           False              1436.0   
944       1985.0  98.0                           False              1174.0   
4136      1973.0  92.0                           False              1323.0   
3157      2007.0  79.0                           False               565.0   
3610      1983.0  90.0                           False               484.0   
3428      1987.0  91.0                           False               313.0   
52        1984.0  82.0                           False               290.0   
4327      2008.0  83.0                           False               361.0   
4768      1974.0  90.0                           False               279.0   

      Number of Artworks Acquired Before Death  
631                                     2432.0  
1449                                    1218.0  
944                                     1160.0  
4136                                    1098.0  
3157                                     489.0  
3610                                     420.0  
3428                                     302.0  
52                                       290.0  
4327                                     289.0  
4768                                     276.0

Yes there are plenty of artists that had their work acquired during their lifetime. The top 10 artists by the number of artworks are shown above, louise bourgeois is the most notable artist in this list, with 2,000+ artworks acquired during her lifetime.

## Clustering

This is a difficult question to answer as it depends on the reason for the analysis, with the reason then used to select features and feature engineering, distance metrics and the cluster optimisation process. For instance should artists be considered similiar based on their mediums, their period, the size/weight of their artwork, their nationality and if the answer is all of the above, how should these be weighted? A naive approach would be to use all of the features and use a kmeans clustering algorithm, but this is not a good approach as it is likely that the clusters will be dominated by the features with the largest variance, and the clusters will not be interpretable. That said, I will use a naive approach to demonstrate the process, and then give an example of a more targeted approach.

### Naive approach

In [250]:
artists = load_artists()
artworks = load_artworks()

artists = add_number_of_artist_works(artists, artworks)
artists = add_artworks_aquired_before_death(artists, artworks)

joined_artists_artworks = pd.merge(artists, artworks, on='Artist ID', how='inner', suffixes=('_artist', '_artwork'))
joined_artists_artworks = add_surface_area_to_joined_artworks(joined_artists_artworks)

Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {'Height (cm)': 206.4}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provided: {}
Invalid combination of dimensions provid

In [240]:
joined_artists_artworks.columns

Index(['Artist ID', 'Name_artist', 'Nationality', 'Gender', 'Birth Year',
       'Death Year', 'age', 'death_before_birth_or_under_10',
       'Number of Artworks', 'Number of Artworks Acquired Before Death',
       'Artwork ID', 'Title', 'Name_artwork', 'Date', 'Medium', 'Dimensions',
       'Acquisition Date', 'Credit', 'Catalogue', 'Department',
       'Classification', 'Object Number', 'Diameter (cm)',
       'Circumference (cm)', 'Height (cm)', 'Length (cm)', 'Width (cm)',
       'Depth (cm)', 'Weight (kg)', 'Duration (s)', 'Year',
       'Surface Area (cm^2)'],
      dtype='object')

In [251]:
max_cardinality = 20
columns_to_exclude = ['Artist ID', 'Name_artist', 'Artwork ID', 'Title', 'Dimensions', 'Credit', 'Object Number', 'Name_artwork', 'Date']
categorical_columns = ['Nationality', 'Gender', 'Medium', 'Classification', 'Department', 'Catalogue']
date_columns = ['Acquisition Date']
numerical_columns = [col for col in joined_artists_artworks.columns if col not in categorical_columns + date_columns + columns_to_exclude]


In [252]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import RobustScaler

# Set index to 'Artist ID'
joined_artists_artworks = joined_artists_artworks.set_index('Artist ID')

# Drop the columns that are not needed
joined_artists_artworks = joined_artists_artworks.drop(columns=columns_to_exclude)

# Reduce the cardinality of the categorical columns
for column in categorical_columns:
    if joined_artists_artworks[column].nunique() > max_cardinality:
        top_categories = joined_artists_artworks[column].value_counts().head(max_cardinality).index
        joined_artists_artworks.loc[~joined_artists_artworks[column].isin(top_categories), column] = 'Other'

# One-hot encode the categorical columns
joined_artists_artworks = pd.get_dummies(joined_artists_artworks, columns=categorical_columns)

# Convert the 'Acquisition Date' column to a 'seconds' column
joined_artists_artworks['Acquisition Date'] = (joined_artists_artworks['Acquisition Date'] - joined_artists_artworks['Acquisition Date'].min()).dt.total_seconds()


# Check that all columns are now numerical
if joined_artists_artworks.select_dtypes(include='object').shape[1] > 0:
    non_numerical_columns = joined_artists_artworks.select_dtypes(include='object').columns
    print(f'The following columns are not numerical: {non_numerical_columns}')


# CScale using the RobustScaler to reduce the effect of outliers
scaler = RobustScaler()
joined_artists_artworks_scaled = scaler.fit_transform(joined_artists_artworks)


# Fill the missing values with the mean (joined_artists_artworks is now a numpy array)
joined_artists_artworks = pd.DataFrame(joined_artists_artworks_scaled, columns=joined_artists_artworks.columns)
joined_artists_artworks = joined_artists_artworks.fillna(joined_artists_artworks.mean())


# Scale all the numerical columns to be between 0 and 1
scaler = MinMaxScaler()
joined_artists_artworks[numerical_columns] = scaler.fit_transform(joined_artists_artworks[numerical_columns])


In [253]:
joined_artists_artworks

Birth Year  Death Year       age  death_before_birth_or_under_10  \
0         0.641844    0.968468  0.915888                             0.0   
1         0.641844    0.968468  0.915888                             0.0   
2         0.641844    0.968468  0.915888                             0.0   
3         0.641844    0.968468  0.915888                             0.0   
4         0.641844    0.968468  0.915888                             0.0   
...            ...         ...       ...                             ...   
142276    0.833333    0.790650  0.699920                             0.0   
142277    0.833333    0.790650  0.699920                             0.0   
142278    0.648860    0.790650  0.699920                             0.0   
142279    0.648860    0.790650  0.699920                             0.0   
142280    0.648860    0.790650  0.699920                             0.0   

        Number of Artworks  Number of Artworks Acquired Before Death  \
0                 0.665874                                   1.00000   
1                 0.665874                                   1.00000   
2                 0.665874                                   1.00000   
3                 0.665874                                   1.00000   
4                 0.665874                                   1.00000   
...                    ...                                       ...   
142276            0.002179                                   0.11012   
142277            0.002179                                   0.11012   
142278            0.000000                                   0.11012   
142279            0.000000                                   0.11012   
142280            0.000000                                   0.11012   

        Acquisition Date  Diameter (cm)  Circumference (cm)  Height (cm)  ...  \
0               0.167539       0.024895            0.424989     0.003195  ...   
1               0.167539       0.024895            0.424989     0.001838  ...   
2               0.167539       0.024895            0.424989     0.002046  ...   
3               0.167539       0.024895            0.424989     0.002035  ...   
4               0.167539       0.024895            0.424989     0.002035  ...   
...                  ...            ...                 ...          ...  ...   
142276          0.736976       0.024895            0.424989     0.002309  ...   
142277          0.736976       0.024895            0.424989     0.002309  ...   
142278          0.718783       0.024895            0.424989     0.004112  ...   
142279          0.543325       0.024895            0.424989     0.000000  ...   
142280          0.543325       0.024895            0.424989     0.000000  ...   

        Department_architecture & design - image archive  Department_drawings  \
0                                                    0.0                  0.0   
1                                                    0.0                  0.0   
2                                                    0.0                  0.0   
3                                                    0.0                  0.0   
4                                                    0.0                  0.0   
...                                                  ...                  ...   
142276                                               0.0                  0.0   
142277                                               0.0                  0.0   
142278                                               0.0                  0.0   
142279                                               0.0                  0.0   
142280                                               0.0                  0.0   

        Department_film  Department_fluxus collection  \
0                   0.0                           0.0   
1                   0.0                           0.0   
2                   0.0                           0.0   
3                   0.0                           0.0   

In [255]:
import numpy as np
from sklearn.neighbors import NearestNeighbors
from sklearn.preprocessing import StandardScaler

def find_optimal_eps(X, min_samples, sample_size=2000):
    """
    Computes and plots the k-distance graph for a given dataset to help
    determine the optimal eps value for DBSCAN.

    Parameters:
    - X: array-like, shape (n_samples, n_features)
        The dataset to compute the k-distance graph for.
    - min_samples: int
        The min_samples parameter for DBSCAN, used to determine k for the k-nearest neighbor calculation.
    - sample_size: int, default=2000
        The number of samples to use for the k-distance graph calculation. If the dataset is larger than this,
        a random sample of sample_size will be used.

    Returns:
    - A plot of the k-distance graph.
    """

    # If the dataset is larger than sample_size, use a random sample of sample_size
    if X.shape[0] > sample_size:
        X_sampled = X.sample(sample_size, random_state=0)
    
    # Compute the nearest neighbors
    k = min_samples - 1
    nearest_neighbors = NearestNeighbors(n_neighbors=k)
    nearest_neighbors.fit(X)
    distances, indices = nearest_neighbors.kneighbors(X_sampled)

    # Sort the distances
    distances = np.sort(distances, axis=0)
    distances = distances[:, -1]  # Get the distance to the k-th nearest neighbor

    # Plot the k-Distance Graph with plotly
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=np.arange(0, len(distances)), y=distances, mode='lines'))
    fig.update_layout(title='k-Distance Graph',
                      xaxis_title='Index',
                      yaxis_title='Distance to k-th nearest neighbor')
    fig.show()

find_optimal_eps(joined_artists_artworks, min_samples=5, sample_size=2000)
    

An elbow plot isnt always very reliable, but at least gives us somewhere to start. A better approach is a qualitative review of the clusters.

In [256]:
# Perform DBSCAN clustering as the number of clusters is not known
from sklearn.cluster import DBSCAN

dbscan = DBSCAN(eps=0.3, min_samples=5)
clusters = dbscan.fit_predict(joined_artists_artworks)

### More targeted approach

In [215]:
joined_artists_artworks = pd.merge(artists, artworks, on='Artist ID', how='inner', suffixes=('_artist', '_artwork'))
# Keep the top 50 mediums and label the rest as 'Other'
top_100_mediums = joined_artists_artworks['Medium'].value_counts().head(100).index
joined_artists_artworks['Medium'] = joined_artists_artworks['Medium'].apply(lambda x: x if x in top_100_mediums else 'Other')


In [169]:
# Group by artist and medium and calculate the number of artworks per medium
artworks_per_artist_per_medium = joined_artists_artworks.groupby(['Artist ID', 'Medium']).size().reset_index(name='Number of Artworks')

# Now calulate the percentage of artworks per medium
total_artworks_per_artist = joined_artists_artworks.groupby('Artist ID').size().reset_index(name='Total Artworks')
artworks_per_artist_per_medium = pd.merge(artworks_per_artist_per_medium, total_artworks_per_artist, on='Artist ID', how='left')
artworks_per_artist_per_medium['Percentage'] = artworks_per_artist_per_medium['Number of Artworks'] / artworks_per_artist_per_medium['Total Artworks'] * 100

# Pivot the table so that each medium is a column, and the values are the percentages, fill the NaN values with 0
artworks_per_artist_per_medium = artworks_per_artist_per_medium.pivot(index='Artist ID', columns='Medium', values='Percentage').fillna(0)
# Disable showing all columns and all column values
pd.set_option('display.max_columns', 20)
pd.set_option('display.max_colwidth', None)
artworks_per_artist_per_medium

Medium     (confirm)  12-inch vinyl record  16mm film  \
Artist ID                                               
1                0.0                   0.0        0.0   
2                0.0                   0.0        0.0   
3                0.0                   0.0        0.0   
4                0.0                   0.0        0.0   
5                0.0                   0.0        0.0   
...              ...                   ...        ...   
67452            0.0                   0.0        0.0   
67453            0.0                   0.0        0.0   
67652            0.0                   0.0      100.0   
67694            0.0                   0.0        0.0   
67695            0.0                   0.0        0.0   

Medium     16mm film (color, sound)  35mm film  35mm film (color, sound)  \
Artist ID                                                                  
1                               0.0        0.0                       0.0   
2                               0.0        0.0                       0.0   
3                               0.0        0.0                       0.0   
4                               0.0        0.0                       0.0   
5                               0.0        0.0                       0.0   
...                             ...        ...                       ...   
67452                           0.0        0.0                       0.0   
67453                           0.0        0.0                       0.0   
67652                           0.0        0.0                       0.0   
67694                           0.0        0.0                       0.0   
67695                           0.0        0.0                       0.0   

Medium     7-inch vinyl record       Other  albumen silver print  \
Artist ID                                                          
1                          0.0   50.000000                   0.0   
2                          0.0    0.000000                   0.0   
3                          0.0  100.000000                   0.0   
4                          0.0  100.000000                   0.0   
5                          0.0   22.222222                   0.0   
...                        ...         ...                   ...   
67452                      0.0   83.333333                   0.0   
67453                      0.0   83.333333                   0.0   
67652                      0.0    0.000000                   0.0   
67694                      0.0  100.000000                   0.0   
67695                      0.0  100.000000                   0.0   

Medium     albumen silver print from a glass negative  ...  \
Artist ID                                              ...   
1                                                 0.0  ...   
2                                                 0.0  ...   
3                                                 0.0  ...   
4                                                 0.0  ...   
5                                                 0.0  ...   
...                                               ...  ...   
67452                                             0.0  ...   
67453                                             0.0  ...   
67652                                             0.0  ...   
67694                                             0.0  ...   
67695                                             0.0  ...   

Medium     transfer lithograph, printed in black  video  \
Artist ID                                                 
1                                            0.0    0.0   
2                                            0.0    0.0   
3                                            0.0    0.0   
4                                            0.0    0.0   
5                                            0.0    0.0   
...                                          ...    ...   
67452                                        0.0    0.0   
67453                                        0

In [170]:
artworks_per_artist_per_medium['Other'].value_counts()

Other
100.000000    5646
0.000000      5083
50.000000      631
33.333333      232
66.666667      213
              ... 
75.390625        1
98.717949        1
1.507538         1
59.602649        1
0.763359         1
Name: count, Length: 708, dtype: int64

Unfortunately 5000 artists will be missed out due to the compression of the Medium column, but this is a necessary step to perform the clustering.

In [194]:
# Perform k-means clustering on the 'artworks_per_artist_per_medium' dataframe
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
from sklearn.metrics.pairwise import pairwise_kernels



artists = pd.read_sql("""SELECT *
                        FROM artists;""", conn)

# Compute dot product kernel matrix - the reason for this is that we want to reward similarity, but not punish dissimilarity
kernel_matrix = pairwise_kernels(artworks_per_artist_per_medium, metric='linear')
# Perform k-means clustering with 20 clusters
kmeans = KMeans(n_clusters=40, init='random', n_init=10)
artworks_per_artist_per_medium['Cluster'] = kmeans.fit_predict(artworks_per_artist_per_medium)

# Merge the 'artworks_per_artist_per_medium' dataframe with the 'artists' dataframe on the 'Artist ID' column
artists_merged = pd.merge(artists, artworks_per_artist_per_medium, left_on='Artist ID', right_on='Artist ID', how='left')

In [195]:
artists_merged['Cluster'].value_counts()

Cluster
1.0     5991
11.0    1174
5.0     1104
4.0      937
6.0      935
17.0     912
9.0      348
36.0     247
29.0     234
28.0     220
21.0     201
37.0     164
33.0     162
24.0     150
16.0     108
10.0     105
27.0     101
0.0      101
14.0      95
3.0       87
13.0      80
26.0      57
7.0       54
25.0      51
2.0       44
31.0      44
32.0      39
38.0      38
18.0      28
30.0      27
22.0      27
35.0      15
39.0      15
12.0      12
15.0      11
34.0      11
20.0      10
19.0       9
23.0       8
8.0        2
Name: count, dtype: int64

In [201]:
cluster = 25
artists_in_cluster = artists_merged[artists_merged['Cluster'] == cluster]
artists_in_cluster

Artist ID                                         Name Nationality  \
622          701                               Alice Boughton    American   
634          713                                Samuel Bourne     British   
772          860                              John G. Bullock    American   
1089        1226                                D. Constantin       Greek   
1139        1283                                George C. Cox    American   
1163        1310                        George P. Critcherson    American   
1188        1337                        Francis Edmund Currey     British   
1351        1524                              Hugh W. Diamond     British   
1412        1592  Dornac (a.k.a. Paul François Arnold Cardon)      French   
1467        1655                                    E. Durand      French   
1469        1657                       Louis-Emile Durandelle      French   
1527        1724                          Peter Henry Emerson     British   
1571        1774                           Frederick H. Evans     British   
1592        1797                                Charles Famin      French   
1926        2163                                 Laura Gilpin    American   
1990        2235                                T. F. Goodall     British   
2583        2890                             Théophile Jaquen      French   
2692        3008                            Gertrude Käsebier    American   
2946        3295                                Kipton Kumler    American   
3178        3554                           Edwin Hale Lincoln    American   
3291        3674                            W. E. Macnaughtan    American   
4226        4711                              William B. Post    American   
4326        4822                               William H. Rau    American   
4340        4839                           Robert S. Redfield    American   
4360        4862                           Oscar G. Rejlander     British   
4445        4963                         Henry Peach Robinson     British   
5114        5699                                  Karl Struss    American   
5168        5760                                  Steve Szabo    American   
5178        5770                            Isaiah West Taber    American   
5215        5812                                       Taupin      French   
5555        6193                            Adam Clark Vroman    American   
5624        6267                           Eva Watson-Schütze    American   
5685        6338                            Clarence H. White    American   
5940        6616                                  Lois Conner    American   
6195        6889                              Victor Schrager    American   
6234        6933                                G. B. Gething     British   
6281        6990                                 Robert Kozma    American   
6800        7664                            John Claude White     British   
6804        7668                               Robert Howlett     British   
6889        7815                             Tommaso Cuccioni     Italian   
6896        7822                               Giorgio Sommer     Italian   
6924        7851                    Frances Benjamin Johnston    American   
7520        8566                            Arthur Wesley Dow    American   
9379       24584                         Gertrude LeRoy Brown    American   
9387       24593                                John P. Heins    American   
9389       24595                           Bernard Shea Horne    American   
9591       26529                              John L. Dunmore    American   
10356      28889                        Charles Dudley Arnold    Canadian   
12034      36206                            H. William Tupper    American   
12035      36218                                Pach Brothers    American   
14891      49390                               Harry R. Barry        None   

  

In [196]:
# Create a 2d TSNE plot of the artists based on the percentage of artworks per medium
from sklearn.manifold import TSNE
from sklearn.preprocessing import StandardScaler
from sklearn.impute import SimpleImputer

# Reduce the dimensionality to 2D
tsne = TSNE(n_components=2, random_state=0)
artworks_per_artist_per_medium_2d = tsne.fit_transform(artworks_per_artist_per_medium.drop(columns='Cluster'))

# Create a dataframe with the 2D data
artworks_per_artist_per_medium_2d = pd.DataFrame(artworks_per_artist_per_medium_2d, columns=['x', 'y'])
artworks_per_artist_per_medium_2d['Artist ID'] = artworks_per_artist_per_medium.index



In [199]:
artworks_per_artist_per_medium_2d = pd.merge(artworks_per_artist_per_medium_2d, artists_merged, on='Artist ID', how='left')

# Plot the 2D data
fig = px.scatter(artworks_per_artist_per_medium_2d, x='x', y='y', color='Cluster', hover_data=['Name_x'], title='2D TSNE Plot of Artists based on the Percentage of Artworks per Medium')
fig.show()